In [2]:
import selenium
from selenium import webdriver
from selenium.webdriver.chrome import service
import time
from selenium.webdriver.common.by import By
from bs4 import BeautifulSoup
import csv
import pandas as pd
from re import findall as re_findall
from datetime import date
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium import webdriver
from selenium.webdriver.chrome.service import Service

In [3]:
def driver_selenium(typ, url):
    try:
        if typ == 'Chrome':
            s=Service('../driver/chromedriver.exe')
            driver = webdriver.Chrome(service=s)
            # driver = webdriver.Chrome(executable_path='../driver/chromedriver.exe')
        elif typ == 'Firefox':
            s=Service('../driver/geckodriver.exe')
            driver = webdriver.Firefox(service=s)
        elif typ == 'Edge':
            s=Service('../driver/msedgedriver')
            driver = webdriver.Edge(service=s)
        driver.get(url)
        return driver
    except:
        print('Loading driver fail')

In [4]:
def linkedin_login(user, password, typ):
    options = webdriver.ChromeOptions()    
    options.add_experimental_option("detach", True) # Keep the page on
    driver = driver_selenium(typ, 'https://www.linkedin.com/')
    
    time.sleep(1)
    driver.find_element(By.XPATH, '/html/body/nav/div/a[2]').click()
    time.sleep(2)
    driver.find_element(By.XPATH, '//*[@id="username"]').send_keys(user)
    time.sleep(2)
    driver.find_element(By.XPATH, '//*[@id="password"]').send_keys(password)
    time.sleep(2)
    driver.find_element(By.XPATH, '//*[@id="organic-div"]/form/div[3]/button').click()
    driver.get('https://www.linkedin.com/jobs/search')
    return driver

def linkedin_search_job_with_login(user, password, typ, job_title, location, time_choose):
    driver = linkedin_login(user, password, typ)
    driver.implicitly_wait(10) # Implicit wait until page loaded
    #time.sleep(3)
       

    
    # Minimal the messaging tab
    time.sleep(5)
    driver.find_elements(By.XPATH, '//button[starts-with(@class,"msg-overlay-bubble-header__control msg-overlay")]')[1].click()
    
    # Filter time
    driver.find_elements(By.XPATH, '//*[@class="search-reusables__primary-filter"]')[1].click() # Drop down list elements
    time.sleep(2)
    
    elements = driver.find_elements(By.XPATH, '//*[@name="date-posted-filter-value"]') # List of all time filters
    if (time_choose=='Month'):
        driver.execute_script("arguments[0].click();", elements[1]) # The second element in the list
    elif (time_choose == 'Week'):
        driver.execute_script("arguments[0].click();", elements[2]) # The third element in the list
    elif (time_choose == 'Day'):
        driver.execute_script("arguments[0].click();", elements[3]) # The four element in the list
        
    time.sleep(3)
    
    driver.find_element(By.XPATH, '//*[@class="artdeco-button artdeco-button--2 artdeco-button--primary ember-view ml2"]').click() # submit result
    time.sleep(3)
    
    # Send job title and location to search
    driver.find_element(By.XPATH, '//input[starts-with(@id,"jobs-search-box-keyword-id")]').clear()
    driver.find_element(By.XPATH, '//input[starts-with(@id,"jobs-search-box-keyword-id")]').send_keys(job_title)
    time.sleep(3)
    driver.find_element(By.XPATH, '//input[starts-with(@id,"jobs-search-box-location-id")]').clear()
    driver.find_element(By.XPATH, '//input[starts-with(@id,"jobs-search-box-location-id")]').send_keys(location)
    time.sleep(3)
    driver.find_element(By.XPATH, '//*[@id="global-nav-search"]/div/div[2]/button[1]').click()
    time.sleep(3)
    
    return driver

In [5]:
def load_one_page_html(soup_general, driver):
    link = soup_general.a['href']
    job_title = soup_general.a.text.strip()
    company_name = soup_general.find(class_ = 'jobs-unified-top-card__company-name').text.strip()
    location = soup_general.find(class_="jobs-unified-top-card__bullet").text.strip()
    date_post = soup_general.find(class_="jobs-unified-top-card__posted-date").text.strip()
    date_retrieved = date.today()
    try:
        number_of_application = soup_general.find(class_="jobs-unified-top-card__applicant-count").text.strip()
    except:
        number_of_application = 0

    type_of_job = soup_general.find_all(class_="jobs-unified-top-card__job-insight")[0].text.strip()
    company_detail = soup_general.find_all(class_="jobs-unified-top-card__job-insight")[1].text.strip()


    # Job description
    job_description = WebDriverWait(driver, 5).until(
                                EC.presence_of_element_located((By.XPATH, '//*[starts-with(@class, "jobs-description__content")]'))
                            )            
    #job_description = driver.find_element(By.XPATH, '//*[starts-with(@class, "jobs-description__content")]')
    job_description_html = job_description.get_attribute('innerHTML')
    soup_job_description = BeautifulSoup(job_description_html, 'lxml')
    job_description_text = soup_job_description.text.strip()

    job = [job_title, company_name, location, job_description_text, link, date_post, date_retrieved, type_of_job, company_detail, number_of_application]
    return job

In [6]:
def load_one_page(job_title, location, typ, elements, driver):
    lst_job = []
    
    # elements = driver.find_elements(By.XPATH, '//*[@class="jobs-search-results__list list-style-none"]/li') # Get all job elements in one page
    
    for i in range(len(elements)):        
        try:
            elements[i].click()
            time.sleep(5)
            job_general = WebDriverWait(driver, 5).until(
                                                    EC.presence_of_element_located((By.XPATH, '//*[@class="jobs-unified-top-card__content--two-pane"]'))
                                                )
            time.sleep(2)
            # job_general = driver.find_element(By.XPATH, '//*[@class="jobs-unified-top-card__content--two-pane"]')
            job_general_html = job_general.get_attribute('innerHTML')
            soup_general = BeautifulSoup(job_general_html, 'lxml')

            link = soup_general.a['href']
            job_title = soup_general.a.text.strip()
            company_name = soup_general.find(class_ = 'jobs-unified-top-card__company-name').text.strip()
            location = soup_general.find(class_="jobs-unified-top-card__bullet").text.strip()
            date_post = soup_general.find(class_="jobs-unified-top-card__posted-date").text.strip()
            date_retrieved = date.today()
            try:
                number_of_application = soup_general.find(class_="jobs-unified-top-card__applicant-count").text.strip()
            except:
                number_of_application = 0

            type_of_job = soup_general.find_all(class_="jobs-unified-top-card__job-insight")[0].text.strip()
            company_detail = soup_general.find_all(class_="jobs-unified-top-card__job-insight")[1].text.strip()


            # Job description
            job_description = WebDriverWait(driver, 5).until(
                                        EC.presence_of_element_located((By.XPATH, '//*[starts-with(@class, "jobs-description__content")]'))
                                    )            
            #job_description = driver.find_element(By.XPATH, '//*[starts-with(@class, "jobs-description__content")]')
            job_description_html = job_description.get_attribute('innerHTML')
            soup_job_description = BeautifulSoup(job_description_html, 'lxml')
            job_description_text = soup_job_description.text.strip()

            job = [job_title, company_name, location, job_description_text, link, date_post, date_retrieved, type_of_job, company_detail, number_of_application]
            lst_job.append(job)
        except:
            print(f'Finally: Element {i} is not loaded properly')
            #driver.execute_script("window.history.go(-2)")
        time.sleep(2)
    #print('Finish page')
    return (lst_job, driver)

In [7]:
def load_one_page_new(driver):
    lst_job = []

    elements = driver.find_elements(By.XPATH, '//*[@class="jobs-search-results__list list-style-none"]/li') # Get all job elements in one page
    
    for i in range(len(elements)):        
        try:
            # elements = driver.find_elements(By.XPATH, '//*[@class="jobs-search-results__list list-style-none"]/li')
            elements[i].click()
            time.sleep(4)
            job_general = WebDriverWait(driver, 5).until(
                                                    EC.presence_of_element_located((By.XPATH, '//*[@class="jobs-unified-top-card__content--two-pane"]'))
                                                )
            # time.sleep(1)
            # job_general = driver.find_element(By.XPATH, '//*[@class="jobs-unified-top-card__content--two-pane"]')
            job_general_html = job_general.get_attribute('innerHTML')
            soup_general = BeautifulSoup(job_general_html, 'lxml')

            job = load_one_page_html(soup_general, driver)
            lst_job.append(job)
        except:
            try:
                print(f'First attemp: Could not find Element {i}')
                #driver.find_element(By.XPATH, f'//button[@aria-label="Page {i}"]').click()
                driver.execute_script("window.history.go(-1)")
                time.sleep(4)
                
                # Second try
                
                elements = driver.find_elements(By.XPATH, '//*[@class="jobs-search-results__list list-style-none"]/li') # Refresh elements
                elements[i].click()
                time.sleep(5)
                job_general = WebDriverWait(driver, 8).until(
                                                        EC.presence_of_element_located((By.XPATH, '//*[@class="jobs-unified-top-card__content--two-pane"]'))
                                                    )
                time.sleep(3)
                # job_general = driver.find_element(By.XPATH, '//*[@class="jobs-unified-top-card__content--two-pane"]')
                job_general_html = job_general.get_attribute('innerHTML')
                soup_general = BeautifulSoup(job_general_html, 'lxml')

                job = load_one_page_html(soup_general) # load job
                
                lst_job.append(job)
            except:
                print(f'Finally: Element {i} is not loaded properly')
            #driver.execute_script("window.history.go(-2)")
        time.sleep(2)
    #print('Finish page')
    return lst_job

In [8]:
def load_full(job_title, location, typ, time_choose):
    
    # Login and search by job title and location
    
    driver = linkedin_search_job_with_login(user, password, typ, job_title, location, time_choose)
    time.sleep(2)
    
    # Get the number of pages
    number_of_page = driver.find_elements(By.XPATH, '//*[@class="artdeco-pagination__pages artdeco-pagination__pages--number"]/li')[-1]
    time.sleep(2)
    source = number_of_page.get_attribute('innerHTML')
    soup = BeautifulSoup(source, 'lxml')
    number_of_page = int(soup.get_text().strip())
    print('Numer of page is', number_of_page)
    #Inital the list
    lst_all_job = []
    
    for i in range(1, number_of_page+1):
        try:
            # Go to page i
            element_page = WebDriverWait(driver, 5).until(
                                        EC.presence_of_element_located((By.XPATH, f'//button[@aria-label="Page {i}"]'))
                                    )
            element_page.click()
            time.sleep(3)
            lst_job = load_one_page_new(driver)
            lst_all_job.append(lst_job)
            print(f'Finish page {i}')
        except:
            print(f'First attemp: Could not find anything from page {i}')
            #driver.find_element(By.XPATH, f'//button[@aria-label="Page {i}"]').click()
            driver.execute_script("window.history.go(-1)")
            time.sleep(4)
            
            # Second try
            
            try:
                element_page = WebDriverWait(driver, 5).until(
                                        EC.presence_of_element_located((By.XPATH, f'//button[@aria-label="Page {i}"]'))
                                    )
                element_page.click()
                time.sleep(5)
                lst_job = load_one_page_new(driver)
                lst_all_job.append(lst_job)
                print(f'Finish page {i}')
            except:
                print(f'Finally: Could not find anything from page {i}')
        time.sleep(8)
    return (lst_all_job, driver)

In [11]:
file = open('../pass/pass_linkedin.txt', 'r')
user = file.readline().strip()
password = file.readline().strip()
typ = 'Chrome'
job_title = 'Data Scientist'
location = 'Germany'
time_choose = 'Week'

In [10]:
linkedin_login(user, password, typ)

<selenium.webdriver.chrome.webdriver.WebDriver (session="530c8c2ab9db8eededf944aad9d03d19")>

In [67]:
driver = linkedin_search_job_with_login(user, password, typ, job_title, location, time_choose)

In [11]:
lst_job = load_one_page_new(driver)

In [12]:
lst_all_job, driver = load_full(job_title, location, typ, time_choose)

Numer of page is 40
Finish page 1
Finish page 2
Finish page 3
Finish page 4
Finish page 5
First attemp: Could not find Element 19
Finally: Element 19 is not loaded properly
First attemp: Could not find Element 20
Finally: Element 20 is not loaded properly
Finish page 6
First attemp: Could not find Element 9
Finally: Element 9 is not loaded properly
First attemp: Could not find Element 10
Finally: Element 10 is not loaded properly
Finish page 7
Finish page 8
Finish page 9
Finish page 10
Finish page 11
Finish page 12
Finish page 13
Finish page 14
Finish page 15
Finish page 16
Finish page 17
Finish page 18
First attemp: Could not find Element 2
Finally: Element 2 is not loaded properly
First attemp: Could not find Element 3
Finally: Element 3 is not loaded properly
Finish page 19
Finish page 20
Finish page 21
Finish page 22
Finish page 23
Finish page 24
First attemp: Could not find Element 2
Finally: Element 2 is not loaded properly
First attemp: Could not find Element 3
Finally: Element 

In [41]:
lst_all_job

[[['(Senior) Data Scientist (m/ f/ d)',
   'Delivery Hero',
   'Berlin, Berlin, Germany',
   "We are looking for Data Scientists (f/m/d) to join the Global Sales & Revenue Data team and revolutionize Sales with data and machine learning. If you're a creative problem solver who is eager to deliver solutions and hungry for a new adventure, an international workplace is waiting for you in the heart of Berlin!\n Build applications, libraries, and services to help deliver impactful data products to our stakeholders in over 50 markets.Build end-to-end ETL pipelines to enable training and running of machine learning models on structured and semi-structured data.Develop measures of data and model quality, and automated tests of the quality of data-powered features.Optimize the reliability, efficiency and agility of machine learning, computational, and data processing pipelines.\nCollaborate with data scientists, data engineers, product managers and business stakeholders to build well-crafted, 

In [14]:
lst_job_data = []
for i in range(len(lst_all_job)):
    lst_job_data +=lst_all_job[i]

df_job = pd.DataFrame(data=lst_job_data, columns=['position', 'company_name', 'location', 'job_description', 'link', 'date_post', 'date_retrived', 'type_of_job', 'company_detail', 'number_of_application'])

In [65]:
lst_job_data

[['Head of Data Science / Chief Data Scientist',
  'Slected.me GmbH',
  'Germany',
  "About us:At Slected.me, we want to help people stop seeing salary as a taboo subject. To do this, we give them the tools and knowledge to better understand their own salary and recognize their own market value in comparison with others. Our goal is to enable a successful and flexible career path for everyone.\nYour Tasks:Design and implement DS/ML solutions that solve our customer's needs (no throwing the model over the fence)Drive progress and set directions for DS/ML projectsWork closely and collaborate with stakeholders to solve their problems and update them on the progressKeep track of recent trends and developments in academia and industry, and identify how to make the most out of it for our business\nYour Profile:Min 5 years of applied experience (industry or equivalent)Good understanding of common ML & stats techniques and their applicationsProficient engineering skillsGood knowledge of standa

In [13]:
for i in range(len(lst_all_job)):
    print(f'Number of element of page {i} is {len(lst_all_job[i])}')

Number of element of page 0 is 25
Number of element of page 1 is 25
Number of element of page 2 is 25
Number of element of page 3 is 25
Number of element of page 4 is 25
Number of element of page 5 is 23
Number of element of page 6 is 23
Number of element of page 7 is 25
Number of element of page 8 is 23
Number of element of page 9 is 21
Number of element of page 10 is 17
Number of element of page 11 is 14
Number of element of page 12 is 11
Number of element of page 13 is 11
Number of element of page 14 is 11
Number of element of page 15 is 11
Number of element of page 16 is 11
Number of element of page 17 is 11
Number of element of page 18 is 9
Number of element of page 19 is 13
Number of element of page 20 is 11
Number of element of page 21 is 11
Number of element of page 22 is 11
Number of element of page 23 is 11
Number of element of page 24 is 8
Number of element of page 25 is 10
Number of element of page 26 is 10
Number of element of page 27 is 11
Number of element of page 28 is 

In [15]:
df_job

position  \
0                        Senior Data Scientist (m/w/d)   
1                    (Senior) Data Scientist (m/ f/ d)   
2                        Senior Data Scientist (m/f/d)   
3    Senior Consultant / Manager (m/w/d) Data Scien...   
4                               Data Scientist (m/f/d)   
..                                                 ...   
572                     Software-Entwickler:in (m/w/d)   
573        Data Engineer / Software Entwickler (w/m/d)   
574                 Freelance-Kotlin Engineer-6 Months   
575       Frontend Engineer - Automation Infra (f/m/d)   
576               Software Engineer Automotive (m/w/d)   

                company_name                               location  \
0                       Atos  Karlsruhe, Baden-Württemberg, Germany   
1              Delivery Hero                Berlin, Berlin, Germany   
2    ProSiebenSat.1 Media SE                Berlin, Berlin, Germany   
3           Capgemini Invent               Munich, Bavaria, Germany   
4                      Bayer                Berlin, Berlin, Germany   
..                       ...                                    ...   
572       WW Consulting GmbH            Leer, Lower Saxony, Germany   
573       ADEAL Systems GmbH           Neu-Isenburg, Hesse, Germany   
574       Darwin Recruitment                Berlin, Berlin, Germany   
575            Delivery Hero                Berlin, Berlin, Germany   
576    GULP – experts united               Dresden, Saxony, Germany   

                                       job_description  \
0    Über Atos\n\nAtos ist ein weltweit führender A...   
1    We are looking for Data Scientists (f/m/d) to ...   
2    Introduction Sentence\n\nIn the ProSiebenSat.1...   
3    Capgemini Invent ist die weltweite Beratungsei...   
4    At Bayer we’re visionaries, driven to solve th...   
..                                                 ...   
572  Als Entwickler bist du direkt dafür verantwort...   
573  Die ADEAL Systems GmbH (ADEAL = Agile Data\n\n...   
574  Apply Now\n\nJob - Kotlin Engineer\n\nClient L...   
575  We are looking for a Frontend Engineer (f/m/d)...   
576  Ihre Aufgaben\n\nEntwicklung von Softwarekompo...   

                                                  link     date_post  \
0    /jobs/view/3098976885/?alternateChannel=search...    4 days ago   
1    /jobs/view/3070186096/?alternateChannel=search...    6 days ago   
2    /jobs/view/3182005003/?alternateChannel=search...    2 days ago   
3    /jobs/view/3179709683/?alternateChannel=search...    3 days ago   
4    /jobs/view/3174076553/?alternateChannel=search...    2 days ago   
..                                                 ...           ...   
572  /jobs/view/3182802000/?alternateChannel=search...  16 hours ago   
573  /jobs/view/3181323378/?alternateChannel=search...     1 day ago   
574  /jobs/view/3077955960/?alternateChannel=search...   6 hours ago   
575  /jobs/view/2806135679/?alternateChannel=search...    6 days ago   
576  /jobs/view/3179756395/?alternateChannel=search...    2 days ago   

    date_retrived                   type_of_job  \
0      2022-07-24                     Full-time   
1      2022-07-24  Full-time · Mid-Senior level   
2      2022-07-24         Full-time · Associate   
3      2022-07-24         Full-time · Associate   
4      2022-07-24       Full-time · Entry level   
..            ...                           ...   
572    2022-07-24       Full-time · Entry level   
573    2022-07-24       Full-time · Entry level   
574    2022-07-24                      Contract   
575    2022-07-24  Full-time · Mid-Senior level   
576    2022-07-24       Full-time · Entry level   

                                        company_detail number_of_application  
0    10,001+ employees · IT Services and IT Consulting          3 applicants  
1              10,001+ employees · Internet Publishing        114 applicants  
2    5,001-10,000 employees · Broadcast Media Produ...         10 applicants  
3    

In [63]:
df_job.to_csv('data_week/linkedin_data_scientist_24_07_Germany.csv', index=False)